In [2]:
import pandas as pd
import numpy as np
from pydynpd import regression
import pathlib
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
import sys

# Assumption tests
## AR
We expect to reject AR(1) but not AR(2).
## Overidentification
A rule of thumb is that any p-value between 0.1 and 0.25 should be fine as it is reasonably larger than a significance level of 0.05 and it is reasonably small enough to not suspect severe p-value inflation. 

In [3]:
unstationary = 'ecgrowth_demeaned logpop_M_diff logpopdens_diff logoutreg_diff democracy_diff'
stationary = 'logmountain ethnic_fractionalization religion_fractionalization language_fractionalization leg_british opec'

columns_to_check = ['onset2COWCS','decade','logpop_M_diff', 'logpopdens_diff', 'logoutreg_diff', 'ecgrowth_demeaned', 'democracy_diff']

path = pathlib.Path().resolve()
# iv = pd.read_csv(str(path).replace("code/Internal_IV", "data") + "/transportIV_file.csv", na_values= '#DIV/0!')

In [4]:
def load_data(predictor):
    df = pd.read_csv(str(path).replace("code/Internal_IV", "data/combined_data") + "/" + predictor + "_data.csv", na_values= '#DIV/0!')
    # df = pd.merge(df, iv, on=["country", "t"])
    
    df[columns_to_check] = df[columns_to_check].replace([np.inf, -np.inf], np.nan)
    df = df.dropna(subset=columns_to_check)
    
    label = le.fit_transform(df['country'])
    df.drop('country', axis=1, inplace=True)
    df['country'] = label
    
    # df = df.set_index(['country', 't'])
    
    # df.fillna(0, inplace=True)
    return df

In [5]:
def reg(method = ' ', additional_cntrl = False, time = False, iv = ' '):
    # System GMM by default (method = "nolevel" produces difference GMM)
    # No stationary controls by default
    # IV = transport by default
    command_str = 'onset2COWCS L(1:?).onset2COWCS s' + sector + ' ' + iv + ' ' + unstationary + ' '
    
    if additional_cntrl:
        command_str = command_str + stationary

    if iv != ' ':
        command_str = command_str + ' | gmm(onset2COWCS, 2:3) gmm(s' + sector + ', 2:3) iv( ' + iv + ' ) '
    else:
        command_str = command_str + ' | gmm(onset2COWCS, 2:3) gmm(s' + sector + ', 2:3) ' 
        
    if method != ' ':
        command_str = command_str + " | " + method     
        if time:
            command_str = command_str + ' timedumm'
    else: 
        if time:
            command_str = command_str + ' | timedumm'
        

    # print(command_str)
    mydpd = regression.abond(command_str, df, ['country', 't']);
    return mydpd #.models[0] #.regression_table

In [6]:
sector = "1"
method = " "
additional_cntrl = False
time = False
iv = " "
command_str = 'onset2COWCS L(1:?).onset2COWCS s' + sector + ' ' + iv + ' ' + unstationary + ' '
    
    
if additional_cntrl:
    command_str = command_str + stationary
if iv != " ":
    command_str = command_str + ' | gmm(onset2COWCS, 2:3) gmm(s' + sector + ', 2:3) iv( ' + iv + ' ) '
else:
    command_str = command_str + ' | gmm(onset2COWCS, 2:3) gmm(s' + sector + ', 2:3) ' 
    
if method != " ":
    command_str = command_str + " | " + method     
    if time:
        command_str = command_str + ' timedumm'
else: 
    if time:
        command_str = command_str + ' | timedumm'
    
command_str
df = load_data("gvcomix")
reg(iv = 'trans_outp_p', time = True);

Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "/Users/zwanran/anaconda3/lib/python3.10/site-packages/IPython/core/interactiveshell.py", line 3460, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/var/folders/94/nn3d0lmn507c2wj_g3d8p2kc0000gn/T/ipykernel_16904/3200574077.py", line 26, in <module>
    reg(iv = 'trans_outp_p', time = True);
  File "/var/folders/94/nn3d0lmn507c2wj_g3d8p2kc0000gn/T/ipykernel_16904/3009798454.py", line 25, in reg
    mydpd = regression.abond(command_str, df, ['country', 't']);
  File "/Users/zwanran/anaconda3/lib/python3.10/site-packages/pydynpd/regression.py", line 47, in __init__
    model = dynamic_panel_model(pdata, variables, user_command.options, com_str, user_command.part_2,
  File "/Users/zwanran/anaconda3/lib/python3.10/site-packages/pydynpd/dynamic_panel_model.py", line 35, in __init__
    self.prepare_data()
  File "/Users/zwanran/anaconda3/lib/python3.10/site-packages/pydynpd/dynamic_panel_model.py", line 48, in prepare_data

In [19]:
def all_reg():
    # world average gvc participation IV.
    # # No time FE if we are using world-level average gvc participation as external IV
    ## System GMM
    m1 = reg(iv = 'avgs' + sector);
    ## Difference GMM
    m2 = reg(iv = 'avgs' + sector, method = "nolevel");

    # Transport IV
    ## System GMM
    m3 = reg(iv = 'trans_outp_p');
    m4 = reg(iv = 'trans_outp_p', time = True);
    ## Difference GMM
    m5 = reg(iv = 'trans_outp_p', method = "nolevel");
    m6 = reg(iv = 'trans_outp_p', time = True, method = "nolevel");
    
    # No external IV
    ## System GMM
    m7 = reg(iv = ' ');
    m8 = reg(time = True);
    ## Difference GMM
    m9 = reg(method = "nolevel");
    m10 = reg(time = True, method = "nolevel");

    results = [m1, m2, m3, m4, m5, m6, m7, m8, m9, m10]
    return results

In [20]:
predictor_list = ["gvcomix", "gvcobp", "gvcofp"]
sector_list = ['1', '2', '6', '10']
results_list = []
for predictor in predictor_list:
    df = load_data(predictor);
    predictor_result = [] ## results for every predictor
                            ## in the order of s1, s2, s6, s10
    for sector in sector_list:
        predictor_result.append(all_reg());
    results_list.append(predictor_result) 
        

 m1
 Dynamic panel-data estimation, two-step system GMM
 Group variable: country                          Number of obs = 1646     
 Time variable: t                                 Min obs per group: 0     
 Number of instruments = 83                       Max obs per group: 13    
 Number of groups = 142                           Avg obs per group: 11.59 
+-------------------+-------------+---------------------+------------+-----------+---+
|    onset2COWCS    |    coef.    | Corrected Std. Err. |     z      |   P>|z|   |   |
+-------------------+-------------+---------------------+------------+-----------+---+
|   L1.onset2COWCS  |  0.0203546  |      0.0317503      | 0.6410837  | 0.5214683 |   |
|         s1        |  -0.0597897 |      0.1852820      | -0.3226957 | 0.7469257 |   |
|       avgs1       |  -0.3871658 |      1.4162941      | -0.2733654 | 0.7845724 |   |
| ecgrowth_demeaned |  -0.2211971 |      0.1016678      | -2.1756853 | 0.0295788 | * |
|   logpop_M_diff   |  5.563555

In [8]:
def print_results(results):
    for s in range(len(results)): # traverse through four sectors
        if s == 0:
            print("\n******sector 1********")
        if s == 1:
            print("\n******sector 2********")
        if s == 2:
            print("\n******sector 6********")
        if s == 3:
            print("\n******sector 10*******")
        for n in range(len(results[s])):
            if n == 0:
                print("IV = World Average; Sys.")
            if n == 1:
                print("IV = World Average; Dif.")
            if n == 3:
                print("IV = Transport; Sys.")
            if n == 4:
                print("IV = Transport; Sys; t-FE.")
            if n == 5:
                print("IV = Transport; Dif.")
            if n == 6:
                print("IV = Transport; Dif; t-FE.")
            if n == 7:
                print("IV = none; Sys.")
            if n == 8:
                print("IV = none; Sys; t-FE.")            
            if n == 9:
                print("IV = none; Dif.")
            if n == 10:
                print("IV = none; Dif; t-FE.")
                
            for l in range(len(results[s][n].models)): # test top 5 models
                m = results[s][n].models[l]
            
                AR1_pass = False
                AR2_pass = False
                Hansen_pass = False

                p_val_AR1 = m.AR_list[0].P_value
                p_val_AR2 = m.AR_list[1].P_value
                p_val_Hansen = m.hansen.p_value
                # if reject AR(1)
                if p_val_AR1 <= .1: 
                    AR1_pass = True
                # IF fail to reject AR(2)
                if p_val_AR2 >= .05:
                    AR2_pass = True
                # if Hansen p-val is between .1 and .25
                if (p_val_Hansen <= .3) & (p_val_Hansen >= .1):
                    Hansen_pass = True
                if AR1_pass & AR2_pass & Hansen_pass:
                    print(m.regression_table)
                    print("AR(1) test P value: ", p_val_AR1, "\n")
                    print("AR(2) test P value: ", p_val_AR2,  "\n")
                    print("Hansen test P value: ", m.hansen.p_value,  "\n")
                    print("\n")
                if AR1_pass == False:
                    print("failed AR1 test, AR(1) p-value: ", p_val_AR1, "\n")
                if AR2_pass == False:
                    print("failed AR2 test, AR(2) p-value: ", p_val_AR2, "\n")
                if Hansen_pass == False:
                    print("failed Hansen test, p-value: ", p_val_Hansen, "\n")
                print("--------------")

In [24]:
for idx in range(len(results_list)):
    sys.stdout = open(str(path).replace("code/Internal_IV", "output/Internal_IV/") +  predictor_list[idx] + ".txt", 'wt')
    print("========Predictor = ", predictor_list[idx], "========")
    print_results(results_list[idx])

In [7]:
def all_reg_add_ctrl():
    # world average gvc participation IV.
    # # No time FE if we are using world-level average gvc participation as external IV
    ## System GMM
    m1 = reg(additional_cntrl=True, iv = 'avgs' + sector);
    ## Difference GMM
    m2 = reg(additional_cntrl=True, iv = 'avgs' + sector, method = "nolevel");

    # Transport IV
    ## System GMM
    m3 = reg(additional_cntrl=True, iv = 'trans_outp_p');
    m4 = reg(additional_cntrl=True, iv = 'trans_outp_p', time = True);
    ## Difference GMM
    m5 = reg(additional_cntrl=True, iv = 'trans_outp_p', method = "nolevel");
    m6 = reg(additional_cntrl=True, iv = 'trans_outp_p', time = True, method = "nolevel");
    
    # No external IV
    ## System GMM
    m7 = reg(additional_cntrl=True, iv = ' ');
    m8 = reg(additional_cntrl=True, time = True);
    ## Difference GMM
    m9 = reg(additional_cntrl=True, method = "nolevel");
    m10 = reg(additional_cntrl=True, time = True, method = "nolevel");

    results = [m1, m2, m3, m4, m5, m6, m7, m8, m9, m10]
    return results

In [9]:
predictor_list = ["gvcomix", "gvcobp", "gvcofp"]
sector_list = ['1', '2', '6', '10']
results_list = []
for predictor in predictor_list:
    df = load_data(predictor);
    predictor_result = [] ## results for every predictor
                            ## in the order of s1, s2, s6, s10
    for sector in sector_list:
        predictor_result.append(all_reg_add_ctrl());
    results_list.append(predictor_result) 
        

 m1
 Dynamic panel-data estimation, two-step system GMM
 Group variable: country                          Number of obs = 1135    
 Time variable: t                                 Min obs per group: 0    
 Number of instruments = 89                       Max obs per group: 13   
 Number of groups = 142                           Avg obs per group: 7.99 
+----------------------------+-------------+---------------------+------------+-----------+----+
|        onset2COWCS         |    coef.    | Corrected Std. Err. |     z      |   P>|z|   |    |
+----------------------------+-------------+---------------------+------------+-----------+----+
|       L1.onset2COWCS       |  -0.0052440 |      0.0054143      | -0.9685475 | 0.3327710 |    |
|             s1             |  -0.3183547 |      0.1722292      | -1.8484363 | 0.0645393 |    |
|           avgs1            |  0.1279697  |      1.3419755      | 0.0953592  | 0.9240295 |    |
|     ecgrowth_demeaned      |  -0.2614495 |      0.0840644   

In [10]:
for idx in range(len(results_list)):
    sys.stdout = open(str(path).replace("code/Internal_IV", "output/Internal_IV/stationary_ctrls") +  predictor_list[idx] + ".txt", 'wt')
    print("========Predictor = ", predictor_list[idx], "========")
    print_results(results_list[idx])